In [1]:
import torch
import torch.nn as nn
torch.cuda.is_available()

True

In [2]:
from transformers import LlamaTokenizer, LlamaForCausalLM
from peft import prepare_model_for_int8_training
tokenizer = LlamaTokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf")
   
tokenizer.pad_token_id = 0
tokenizer.padding_side = 'left'

model = LlamaForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
    torch_dtype=torch.float16
)

model = prepare_model_for_int8_training(model)

/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /opt/conda did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 113
CUDA SETUP: Loading binary /home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/libbitsandbytes_cuda113.so...


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [3]:
import random
import json

# defined by WikiSQL

agg_ops = ['', 'MAX', 'MIN', 'COUNT', 'SUM', 'AVG']
cond_ops = ['=', '>', '<', 'OP']
syms = ['SELECT', 'WHERE', 'AND', 'COL', 'TABLE', 'CAPTION', 'PAGE', 'SECTION', 'OP', 'COND', 'QUESTION', 'AGG', 'AGGOPS', 'CONDOPS']

def fix_repr(d,cols,types,tid):
    sel_index=d['sel'] 
    agg_index=d['agg']
    conditions=d['conds']
    col = cols[sel_index]
    rep = 'SELECT {agg} {sel} FROM {tid}'.format(
            agg=agg_ops[agg_index],
            sel=col,
            tid=tid
            )
    if conditions:
        cs = []
        for i, o, v in conditions:
            #print(i,cols)
            nm = cols[i]
            op = cond_ops[o]
            
            if types[i] in ['text']:
                val = f"\'{v}\'"
            else:
                val = v
            cs.append(f'{nm} {op} {val}')
        #print(cs)

        rep +=  ' WHERE ' + ' AND '.join(cs)
    
    return rep

tbl_cols = {}
tbl_types = {}
tbl_str = {}

prefix = 'Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.'

def tbl_def_to_string(id, header, types):
    s = f'table: {id}\ncolumns: ' + ','.join(header)
    return s

with open('data/train.tables.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['id']
        hdr = js['header']
        ts = js['types']
        tbl_str[id] = tbl_def_to_string(id,hdr,ts)
        tbl_cols[id] = hdr
        tbl_types[id] = ts

q_s = []
a_s = []

with open('data/train.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['table_id']
        s = tbl_str[id]
        qst = js['question']
        nl = s + '\nQ: ' + qst + '\nA: '
        q_s.append(nl)

        sql = js['sql']
        a = fix_repr(sql,tbl_cols[id],tbl_types[id],id)
        a = a + "\nEND\n"
        a_s.append(a)

M = len(q_s)

data_txt = [q_s[i] + a_s[i] for i in range(M)]

for i in range(5):
    j = random.randint(0,M-1)
    print()
    print(data_txt[j]) 
        
   


table: 2-1137692-1
columns: Entrant,Constructor,Chassis,Engine †,Tyre,Driver,Rounds
Q: What were the rounds on the Engine † of the Ferrari 048?
A: SELECT  Rounds FROM 2-1137692-1 WHERE Engine † = 'ferrari 048'
END


table: 1-21530474-1
columns: Chassis code,Model no.,Production years,Drivetrain,Transmission,Engine type,Engine code,Region(s)
Q: Name the drivetrain for 1ur-fse for usf41
A: SELECT  Drivetrain FROM 1-21530474-1 WHERE Engine code = '1UR-FSE' AND Chassis code = 'USF41'
END


table: 2-14155087-1
columns: Callsign,Area served,Frequency,Band,On-air ID,Purpose
Q: What is the Callsign with an Area of tamworth and frequency of 0 88.9?
A: SELECT  Callsign FROM 2-14155087-1 WHERE Area served = 'tamworth' AND Frequency = '0 88.9'
END


table: 2-17580726-2
columns: Date,Opponent,Venue,Score,Attendance,Scorers
Q: What is the number of people in attendance when Tonbridge Angels is the opponent?
A: SELECT  Attendance FROM 2-17580726-2 WHERE Opponent = 'tonbridge angels'
END


table: 1-2

In [4]:
toks = [tokenizer(s) for s in data_txt]


In [5]:
import numpy as np
import pandas as pd

print(len(toks[0].input_ids))
lens = np.array([len(tok.input_ids) for tok in toks])
print(pd.DataFrame(lens).describe())

z = zip(q_s,lens)
q_red = [a for a,b in z if b < 100]
z = zip(a_s,lens)
a_red = [a for a,b in z if b < 100]

data_red = [q_red[i] + a_red[i] for i in range(len(q_red))]
print(len(data_red))



92
                  0
count  56355.000000
mean     101.219519
std       21.740325
min       63.000000
25%       87.500000
50%       97.000000
75%      109.000000
max      461.000000
32084


In [6]:
import random, datasets
#d = {'prompt': random.sample(data_red, 1000)}
d = {'prompt': data_red}

data = datasets.Dataset.from_dict(d)
data = data.map(lambda x:
        tokenizer(
        x['prompt'],
        truncation=True,
        max_length=100,
        padding="max_length"
        ))

data = data.remove_columns('prompt')


Map:   0%|          | 0/32084 [00:00<?, ? examples/s]

In [7]:
from peft import LoraConfig, get_peft_model
import transformers
import datasets

LORA_R = 4
LORA_ALPHA = 16
LORA_DROPOUT = .1
CUTOFF_LEN = 256
BATCH = 128
MICRO_BATCH = 4
N_GAS = BATCH//MICRO_BATCH
EPOCHS = 1
LR = 1e-4

lora_cfg = LoraConfig(
    r = LORA_R,
    lora_alpha=LORA_ALPHA,
    lora_dropout=LORA_DROPOUT,
    task_type='CASUAL_LM',
    target_modules=['q_proj','v_proj']
)

model = get_peft_model(model,lora_cfg)

targs = transformers.TrainingArguments(
    per_device_train_batch_size=MICRO_BATCH,
    gradient_accumulation_steps=N_GAS,
    warmup_steps=0,
    num_train_epochs=EPOCHS,
    learning_rate=LR,
    fp16=True,
    logging_steps=1,
    output_dir='sqllama-out2',
    save_total_limit=3,
    remove_unused_columns=False
)


In [8]:
trainer = transformers.Trainer(
    model = model,
    train_dataset = data,
    args = targs,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False)
)
trainer.train(resume_from_checkpoint=False)
model.save_pretrained('sqllama-out2')

In [11]:
def get_query(q):
    
    toks = tokenizer(q , return_tensors='pt')
    ctoks = toks.input_ids.to('cuda')
    gen = model.generate(ctoks, max_length=100)
    return tokenizer.decode(gen[0])

M = len(q_red)

for _ in range(10):
    j = random.randint(0,M-1)
    qs = q_red[j]
    a = a_red[j]

    ma = get_query(qs)

    #print(qs)
    print('from model')
    print(ma)
    print()
    print('expected answer')
    print(a)


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")


from model
<unk>table: 1-12028543-3
columns: Season,Cup FinalDate,WinningTeam,Score,LosingTeam,Location,Cup Final Attendance
Q: Who was the winning team in the 1989 season?
A:  SELECT  WinningTeam FROM 1-12028543-3 WHERE Season = '1989'
END
END
END
END

expected answer
SELECT  WinningTeam FROM 1-12028543-3 WHERE Season = '1989'
END

from model
<unk>table: 2-18096431-5
columns: Place,Player,Country,Score,To par
Q: What is To par, when Country is "United States", and when Player is "Mark Brooks"?
A: 18-1
END


expected answer
SELECT  To par FROM 2-18096431-5 WHERE Country = 'united states' AND Player = 'mark brooks'
END

from model
<unk>table: 2-10701914-2
columns: Home team,Home team score,Away team,Away team score,Venue,Crowd,Date
Q: What home team played at the western oval?
A:  Western Bulldogs
END
END
END
END
END
END
END
END
END
END
END
END
END
END
END
END
END


expected answer
SELECT  Home team FROM 2-10701914-2 WHERE Venue = 'western oval'
END

from model
<unk>table: 1-29598261-1
